In [3]:
from transformers import AutoProcessor, AutoModelForCausalLM
import gradio as gr
import torch

# Load the processor and model
processor = AutoProcessor.from_pretrained("microsoft/git-base")
model = AutoModelForCausalLM.from_pretrained("./")

def predict(image):
    try:
        # Prepare the image using the processor
        inputs = processor(images=image, return_tensors="pt")

        # Move inputs to the appropriate device
        device = "cuda" if torch.cuda.is_available() else "cpu"
        inputs = {key: value.to(device) for key, value in inputs.items()}
        model.to(device)

        # Generate the caption
        outputs = model.generate(**inputs)

        # Decode the generated caption
        caption = processor.batch_decode(outputs, skip_special_tokens=True)[0]

        return caption

    except Exception as e:
        print("Error during prediction:", str(e))
        return "Error: " + str(e)

# https://www.gradio.app/guides
with gr.Blocks() as demo:
    image = gr.Image(type="pil")
    predict_btn = gr.Button("Predict", variant="primary")
    output = gr.Label(label="Generated Caption")

    inputs = [image]
    outputs = [output]

    predict_btn.click(predict, inputs=inputs, outputs=outputs)

if __name__ == "__main__":
    demo.launch()  # Local machine only
    # demo.launch(server_name="0.0.0.0")  # LAN access to local machine
    # demo.launch(share=True)  # Public access to local machine


Running on local URL:  http://127.0.0.1:7862

To create a public link, set `share=True` in `launch()`.
